In [18]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import csv
import json
%matplotlib inline

In [19]:
#import csv
df1 = pd.read_csv('data_exp_6138-v31_task-2jau.csv', sep = ",")
df2 = pd.read_csv('data_exp_6138-v31_task-5e3j.csv', sep = ",")
df1.head(1)

Event Index     UTC Timestamp             UTC Date   Local Timestamp  \
0           1 1551893943680.000  06/03/2019 17:39:03 1551893943135.000   

   Local Timezone           Local Date  Experiment ID  Experiment Version  \
0           0.000  06/03/2019 17:39:03       6138.000              31.000   

  Tree Node Key  Repeat Key  Schedule ID     Participant Public ID  \
0     task-2jau         nan  2280330.000  5c0e55c7427e7b00013b7cb0   

   Participant Private ID  Participant Starting Group Participant Status  \
0              621711.000                         nan           complete   

   Participant Completion Code Participant External Session ID  \
0                          nan        5c8003740fa63e001663059f   

  Participant Device Type Participant Device Participant OS  \
0                computer  Desktop or Laptop     Windows 10   

    Participant Browser Participant Monitor Size Participant Viewport Size  \
0  Chrome 72.0.3626.121                 1280x720                  1280x578   

            Checkpoint             Task Name  Task Version randomiser-mgaa  \
0  after questionnairs  High to Low with rod        10.000     High to Low   

  checkpoint-z52s     checkpoint-u6nu checkpoint-puaw checkpoint-axcr  \
0   after consent  after demographics  after training   after fishing   

       checkpoint-mrc4  reaction time  key pressed  price_displayed     order  \
0  after questionnairs       7893.000       32.000              nan  high-low   

  environment  round instance task  function id  rod fixing checked  \
0        high             nan  NaN  instruction                 nan   

   builtin rt          end_time        start_time  
0    7892.480 1551893943134.000 1551893935241.000

In [20]:
#get rid of scientific notation
pd.set_option('display.float_format', lambda x: '%.3f' % x)

#replace all null and nan to the np.nan
df1 = df1.replace('null', np.nan)
df1 = df1.replace('nan', np.nan)
df2 = df2.replace('null', np.nan)
df2 = df2.replace('nan', np.nan)

#turn object into floats and round them 
df1['end_time'] = round(df1['end_time'].astype(float))
df1['start_time'] = round(df1['start_time'].astype(float))
df1['builtin_rt'] = df1['builtin rt'].astype(float) #dont round up builtin reaction time
df1['quality_check'] = df1['rod fixing checked'].astype(float)
df1['id'] = df1['Participant Private ID']
df1['function_id'] = df1['function id']
df1['round_instance'] = df1['round instance']
df2['end_time'] = round(df2['end_time'].astype(float))
df2['start_time'] = round(df2['start_time'].astype(float))
#df2['builtin_rt'] = df2['builtin rt'].astype(float) #dont round up builtin reaction time
df2['quality_check'] = df2['rod fixing checked'].astype(float)
df2['id'] = df2['Participant Private ID']
df2['round_instance'] = df2['round_instance']
df2['function_id'] = df2['function id']

In [21]:
#pd.set_option('display.max_columns', 300)
#pd.set_option('display.max_rows', None)

In [22]:
#select columns from df1 and df2

data1 = df1[['id','price_displayed', 'key pressed','environment', 'order', 
           'round_instance', 'task', 'function_id', 'quality_check', 
           'builtin_rt', 'end_time', 'start_time', 'Participant Public ID']]
data2 = df2[['id','price_displayed', 'key pressed','environment', 'order', 
           'round_instance', 'task', 'function_id', 'quality_check', 
           'builtin_rt', 'end_time', 'start_time', 'Participant Public ID']]

In [23]:
#append two csv files into one
#dont append all the columns in two files --> way too big and no real meaning
data = data1.append(data2)

In [24]:
pd.set_option('display.max_columns', 300)
pd.set_option('display.max_rows', None)
#data.head(10000)

In [25]:
#get rid of all data collected from caller function
#caller functions were used to initilized elements - dont have real meaning to us
data = data[data.function_id != 'caller']
data = data[pd.notnull(data['function_id'])]

In [26]:
def latency(ser):
    """ takes in a series and turn into a list
    then calculate latency
    the same function in pandas is called np.diff()
    """
    lst = ser.tolist()
    i = 0
    latency_s = []
    while i < len(lst)-1:
        if lst[i] != np.nan:
            t = lst[i+1] - lst[i]
            latency_s.append(t)
            i = i + 1
        else:
            latency_s.append(np.nan)
    latency_s.append(0)
    return latency_s

In [ ]:
#data_rod.set_index(['id'])

In [ ]:
# seperate data into seperate instances
# data_rod_11 = data_rod[data_rod.round_instance == 11]
# data_rod_21 = data_rod[data_rod.round_instance == 21]
# data_rod_12 = data_rod[data_rod.round_instance == 12]
# data_rod_22 = data_rod[data_rod.round_instance == 22]

In [ ]:
#data_rod_11.head(1000)
# np.diff([1, 9, 10, 12, 15])

In [ ]:
# m = drop_first_last(d['start_time'], 8)
# id_e = drop_first_last(data_rod['id'], 8)
# environment = drop_first_last(data_rod['environment'], 8)
# round_instance = drop_first_last(data_rod['round_instance'], 8)
# quality_check = drop_first_last(data_rod['quality_check'], 8)
# start_time = drop_first_last(data_rod['start_time'], 8)
# end_time = drop_first_last(data_rod['end_time'], 8)
# #d = {'id': id_e, 'environment': environment, 'round_instance': round_instance, 'quality_check': quality_check,
# #   'start_time': start_time, 'end_time':end_time, 'latency': d}
# #data_rod_final = pd.DataFrame(data=d)
# len(environment)

In [27]:
#take a look at rod fixing data
data_rod = data[data.function_id == "rod_fixing"]


In [28]:
#do a data quality check
def quality_check(lst):
    check = lst.tolist()
    if 0 in check:
        return True
    else:
        return False
quality_check(data_rod['quality_check'])
# false - they all fixed their rods

data_rod.head(10000)

id  price_displayed  key pressed environment     order  \
187   621711.000              nan       39.000        high  high-low   
188   621711.000              nan       39.000        high  high-low   
189   621711.000              nan       39.000        high  high-low   
190   621711.000              nan       39.000        high  high-low   
191   621711.000              nan       39.000        high  high-low   
192   621711.000              nan       39.000        high  high-low   
193   621711.000              nan       39.000        high  high-low   
194   621711.000              nan       39.000        high  high-low   
540   621711.000              nan       39.000        high  high-low   
541   621711.000              nan       39.000        high  high-low   
542   621711.000              nan       39.000        high  high-low   
543   621711.000              nan       39.000        high  high-low   
544   621711.000              nan       39.000        high  high-low   
545   621711.000              nan       39.000        high  high-low   
546   621711.000              nan       39.000        high  high-low   
547   621711.000              nan       39.000        high  high-low   
889   621711.000              nan       39.000        high  high-low   
890   621711.000              nan       39.000        high  high-low   
891   621711.000              nan       39.000        high  high-low   
892   621711.000              nan       39.000        high  high-low   
893   621711.000              nan       39.000        high  high-low   
894   621711.000              nan       39.000        high  high-low   
895   621711.000              nan       39.000        high  high-low   
896   621711.000              nan       39.000        high  high-low   
1329  621711.000              nan       39.000        high  high-low   
1330  621711.000              nan       39.000        high  high-low   
1331  621711.000              nan       39.000        high  high-low   
1332  621711.000              nan       39.000        high  high-low   
1333  621711.000              nan       39.000        high  high-low   
1334  621711.000              nan       39.000        high  high-low   
1335  621711.000              nan       39.000        high  high-low   
1336  621711.000              nan       39.000        high  high-low   
1687  621711.000              nan       39.000        high  high-low   
1688  621711.000              nan       39.000        high  high-low   
1689  621711.000              nan       39.000        high  high-low   
1690  621711.000              nan       39.000        high  high-low   
1691  621711.000              nan       39.000        high  high-low   
1692  621711.000              nan       39.000        high  high-low   
1693  621711.000              nan       39.000        high  high-low   
1694  621711.000              nan       39.000        high  high-low   
1916  621711.000              nan       39.000        high  high-low   
1917  621711.000              nan       39.000        high  high-low   
1918  621711.000              nan       39.000        high  high-low   
1919  621711.000              nan       39.000        high  high-low   
1920  621711.000              nan       39.000        high  high-low   
1921  621711.000              nan       39.000        high  high-low   
1922  621711.000              nan       39.000        high  high-low   
1923  621711.000              nan       39.000        high  high-low   
2250  621711.000              nan       39.000         low  high-low   
2251  621711.000              nan       39.000         low  high-low   
2252  621711.000              nan       39.000         low  high-low   
2253  621711.000              nan       39.000         low  high-low   
2254  621711.000              nan       39.000         low  high-low   
2255  621711.000              nan       39.000         low  high-low   
2256  621711.000              nan       39.000        

In [57]:
data_rod.groupby('round_instance')['id'].size()

round_instance
11.000    702
12.000    765
21.000    722
22.000    695
Name: id, dtype: int64

In [62]:
data_rod.groupby('id')['start_time'].size()

id
621711.000     91
621725.000     84
621729.000     83
621733.000     94
621734.000     92
621735.000     79
621738.000     88
621749.000     92
621753.000     94
621759.000     95
621761.000     92
621762.000     87
621770.000     90
621772.000     97
621774.000    101
621775.000     94
621785.000     89
621789.000     85
625385.000     86
625386.000     96
625389.000     90
625392.000     86
625394.000     92
625395.000    110
625403.000     75
625404.000     85
625406.000     83
625408.000     84
625410.000    113
625411.000     84
625416.000     79
625431.000     94
Name: start_time, dtype: int64

In [63]:
data_rod[data_rod.id == 621774.000]

id  price_displayed  key pressed environment     order  \
26597 621774.000              nan       40.000        high  high-low   
26598 621774.000              nan       40.000        high  high-low   
26602 621774.000              nan       39.000        high  high-low   
26603 621774.000              nan       39.000        high  high-low   
26604 621774.000              nan       39.000        high  high-low   
26605 621774.000              nan       39.000        high  high-low   
26606 621774.000              nan       39.000        high  high-low   
26607 621774.000              nan       39.000        high  high-low   
26608 621774.000              nan       39.000        high  high-low   
26609 621774.000              nan       39.000        high  high-low   
26968 621774.000              nan       39.000        high  high-low   
26969 621774.000              nan       39.000        high  high-low   
26970 621774.000              nan       39.000        high  high-low   
26971 621774.000              nan       39.000        high  high-low   
26972 621774.000              nan       39.000        high  high-low   
26973 621774.000              nan       39.000        high  high-low   
26974 621774.000              nan       39.000        high  high-low   
26975 621774.000              nan       39.000        high  high-low   
27317 621774.000              nan       39.000        high  high-low   
27318 621774.000              nan       39.000        high  high-low   
27319 621774.000              nan       39.000        high  high-low   
27320 621774.000              nan       39.000        high  high-low   
27321 621774.000              nan       39.000        high  high-low   
27322 621774.000              nan       39.000        high  high-low   
27323 621774.000              nan       39.000        high  high-low   
27324 621774.000              nan       39.000        high  high-low   
27751 621774.000              nan       39.000        high  high-low   
27752 621774.000              nan       39.000        high  high-low   
27753 621774.000              nan       39.000        high  high-low   
27754 621774.000              nan       39.000        high  high-low   
27755 621774.000              nan       39.000        high  high-low   
27756 621774.000              nan       39.000        high  high-low   
27757 621774.000              nan       39.000        high  high-low   
27758 621774.000              nan       39.000        high  high-low   
28107 621774.000              nan       39.000        high  high-low   
28108 621774.000              nan       39.000        high  high-low   
28109 621774.000              nan       39.000        high  high-low   
28110 621774.000              nan       39.000        high  high-low   
28111 621774.000              nan       39.000        high  high-low   
28112 621774.000              nan       39.000        high  high-low   
28113 621774.000              nan       39.000        high  high-low   
28114 621774.000              nan       39.000        high  high-low   
28375 621774.000              nan       39.000        high  high-low   
28376 621774.000              nan       39.000        high  high-low   
28377 621774.000              nan       39.000        high  high-low   
28378 621774.000              nan       39.000        high  high-low   
28379 621774.000              nan       39.000        high  high-low   
28380 621774.000              nan       39.000        high  high-low   
28381 621774.000              nan       39.000        high  high-low   
28382 621774.000              nan       39.000        high  high-low   
28710 621774.000              nan       39.000         low  high-low   
28711 621774.000              nan       39.000         low  high-low   
28712 621774.000              nan       39.000         low  high-low   
28713 621774.000              nan       39.000         low  high-low   
28714 621774.000              nan       39.000        

In [61]:
data_rod[data_rod.id == 621729.000].groupby('round_instance').size()


round_instance
11.000    14
12.000    29
21.000    21
22.000    19
dtype: int64

In [29]:
rod_group = data_rod[['id', 'start_time']]
#rod_group = rod_group.sort_values(by = ['id', 'start_time'])
rod_group.head(1000)


id        start_time
187   621711.000 1551893991468.000
188   621711.000 1551893992389.000
189   621711.000 1551893992527.000
190   621711.000 1551893992669.000
191   621711.000 1551893992792.000
192   621711.000 1551893992933.000
193   621711.000 1551893993068.000
194   621711.000 1551893993202.000
540   621711.000 1551894043746.000
541   621711.000 1551894044599.000
542   621711.000 1551894044861.000
543   621711.000 1551894045000.000
544   621711.000 1551894045123.000
545   621711.000 1551894045241.000
546   621711.000 1551894045386.000
547   621711.000 1551894045544.000
889   621711.000 1551894096015.000
890   621711.000 1551894096750.000
891   621711.000 1551894096896.000
892   621711.000 1551894097034.000
893   621711.000 1551894097178.000
894   621711.000 1551894097316.000
895   621711.000 1551894097455.000
896   621711.000 1551894097765.000
1329  621711.000 1551894186663.000
1330  621711.000 1551894187361.000
1331  621711.000 1551894187515.000
1332  621711.000 1551894187659.000
1333  621711.000 1551894187798.000
1334  621711.000 1551894187921.000
1335  621711.000 1551894188048.000
1336  621711.000 1551894188190.000
1687  621711.000 1551894238898.000
1688  621711.000 1551894240028.000
1689  621711.000 1551894240159.000
1690  621711.000 1551894240279.000
1691  621711.000 1551894240404.000
1692  621711.000 1551894240545.000
1693  621711.000 1551894240674.000
1694  621711.000 1551894240810.000
1916  621711.000 1551894278052.000
1917  621711.000 1551894278745.000
1918  621711.000 1551894278877.000
1919  621711.000 1551894278999.000
1920  621711.000 1551894279141.000
1921  621711.000 1551894279264.000
1922  621711.000 1551894279394.000
1923  621711.000 1551894279545.000
2250  621711.000 1551894404708.000
2251  621711.000 1551894405457.000
2252  621711.000 1551894405626.000
2253  621711.000 1551894405777.000
2254  621711.000 1551894405908.000
2255  621711.000 1551894406037.000
2256  621711.000 1551894406185.000
2257  621711.000 1551894406328.000
2570  621711.000 1551894457081.000
2571  621711.000 1551894458046.000
2572  621711.000 1551894458155.000
2573  621711.000 1551894458281.000
2574  621711.000 1551894458410.000
2842  621711.000 1551894509402.000
2843  621711.000 1551894510284.000
2844  621711.000 1551894510434.000
2845  621711.000 1551894510555.000
2846  621711.000 1551894510690.000
2847  621711.000 1551894510802.000
2848  621711.000 1551894510920.000
2849  621711.000 1551894511033.000
3216  621711.000 1551894577995.000
3217  621711.000 1551894578706.000
3218  621711.000 1551894578816.000
3219  621711.000 1551894578961.000
3220  621711.000 1551894579079.000
3221  621711.000 1551894579194.000
3222  621711.000 1551894579312.000
3546  621711.000 1551894630227.000
3547  621711.000 1551894630806.000
3548  621711.000 1551894630930.000
3549  621711.000 1551894631055.000
3550  621711.000 1551894631180.000
3551  621711.000 1551894631324.000
3552  621711.000 1551894631467.000
3553  621711.000 1551894631617.000
3770  621711.000 1551894669417.000
3771  621711.000 1551894670227.000
3772  621711.000 1551894670334.000
3773  621711.000 1551894670463.000
3774  621711.000 1551894670592.000
3775  621711.000 1551894670714.000
3776  621711.000 1551894670839.000
179   621725.000 1551894191511.000
180   621725.000 1551894192358.000
181   621725.000 1551894192451.000
182   621725.000 1551894192579.000
183   621725.000 1551894192700.000
184   621725.000 1551894192813.000
185   621725.000 1551894192939.000
186   621725.000 1551894193069.000
543   621725.000 1551894243813.000
544   621725.000 1551894244560.000
545   621725.000 1551894244691.000
546   621725.000 1551894244823.000
547   621725.000 1551894244967.000
548   621725.000 1551894245109.000
549   621725.000 1551894245237.000
550   621725.000 1551894245392.000
893   621725.000 1551894296060.000
897   621725.000 1551894296265.000
898   621725.000 1551894296825.000
899   621725.000 1551894296946.000
900   621725.000 1551894297088.000
901   621725.000 1551894297225.000
902   621725.000 1551894

In [30]:
a = rod_group.groupby('id', as_index = True)['start_time'].diff().shift(-1).reset_index(name = 'latency')
#g = data_rod.groupby('id')['start_time'].diff().to_frame()
a = a.set_index('index')
a.head(100000)

latency
index           
187      921.000
188      138.000
189      142.000
190      123.000
191      141.000
192      135.000
193      134.000
194    50544.000
540      853.000
541      262.000
542      139.000
543      123.000
544      118.000
545      145.000
546      158.000
547    50471.000
889      735.000
890      146.000
891      138.000
892      144.000
893      138.000
894      139.000
895      310.000
896    88898.000
1329     698.000
1330     154.000
1331     144.000
1332     139.000
1333     123.000
1334     127.000
1335     142.000
1336   50708.000
1687    1130.000
1688     131.000
1689     120.000
1690     125.000
1691     141.000
1692     129.000
1693     136.000
1694   37242.000
1916     693.000
1917     132.000
1918     122.000
1919     142.000
1920     123.000
1921     130.000
1922     151.000
1923  125163.000
2250     749.000
2251     169.000
2252     151.000
2253     131.000
2254     129.000
2255     148.000
2256     143.000
2257   50753.000
2570     965.000
2571     109.000
2572     126.000
2573     129.000
2574   50992.000
2842     882.000
2843     150.000
2844     121.000
2845     135.000
2846     112.000
2847     118.000
2848     113.000
2849   66962.000
3216     711.000
3217     110.000
3218     145.000
3219     118.000
3220     115.000
3221     118.000
3222   50915.000
3546     579.000
3547     124.000
3548     125.000
3549     125.000
3550     144.000
3551     143.000
3552     150.000
3553   37800.000
3770     810.000
3771     107.000
3772     129.000
3773     129.000
3774     122.000
3775     125.000
3776         nan
179      847.000
180       93.000
181      128.000
182      121.000
183      113.000
184      126.000
185      130.000
186    50744.000
543      747.000
544      131.000
545      132.000
546      144.000
547      142.000
548      128.000
549      155.000
550    50668.000
893      205.000
897      560.000
898      121.000
899      142.000
900      137.000
901      150.000
902      126.000
903      147.000
904    77358.000
1365    1099.000
1366     126.000
1367     127.000
1368     131.000
1369     142.000
1370     130.000
1371     143.000
1372   50470.000
1719     600.000
1720     139.000
1721     146.000
1722     139.000
1723     117.000
1724     167.000
1725     142.000
1726   37833.000
1979     833.000
1980     122.000
1981     144.000
1982     107.000
1983     132.000
1984     163.000
1985     147.000
1986  101693.000
2335     574.000
2336     134.000
2337     124.000
2338     121.000
2339     127.000
2340   51321.000
2713    1092.000
2714     128.000
2715     136.000
2716     136.000
2717     169.000
2718     154.000
2719   50491.000
3055     748.000
3056     117.000
3057     136.000
3058     135.000
3059     132.000
3060     144.000
3061     135.000
3062   96031.000
3508     752.000
3509   51501.000
3858     784.000
3859   38545.000
4123    1022.000
4124     127.000
4125     127.000
4126     119.000
4127     111.000
4128     135.000
4129         nan
894          nan
895          nan
896          nan
4072     745.000
4073     135.000
4074     132.000
4075     108.000
4076   51181.000
4387   52268.000
4697     560.000
4698     157.000
4699     138.000
4700     150.000
4701     141.000
4702     159.000
4703     158.000
4704   80060.000
5060     165.000
5061     190.000
5065     475.000
5066     149.000
5067     160.000
5068     143.000
5069     154.000
5070     145.000
5071   51137.000
5372     583.000
5373     136.000
5374     126.000
5375     139.000
5376   38317.000
5606     569.000
5607     135.000
5608     136.000
5609  101444.000
5921     401.000
5922     163.000
5923     136.000
5924     140.000
5925     134.000
5926     135.000
5927   50242.000
6234     171.000
6235     173.000
6236     156.000
6237     167.000
6238     170.000
6239     140.000
6243     747.000
6244     113.000
6245     123.000
6246     136.000
6247     144.000
6248   51087.000
6568     540.000
6569     123.000
6570     139.000
6571     155.000
6572     160.000
6573     156.000
6574   81652.000
6946     577.0

In [ ]:
1551894044599.000 - 1551894043746.000

In [31]:
rod_group['latency'] = a['latency']
#rod_group = rod_group.sort_index().sort_values(['id', 'start_time'])
rod_group.head(100000)

id        start_time    latency
187   621711.000 1551893991468.000    921.000
188   621711.000 1551893992389.000    138.000
189   621711.000 1551893992527.000    142.000
190   621711.000 1551893992669.000    123.000
191   621711.000 1551893992792.000    141.000
192   621711.000 1551893992933.000    135.000
193   621711.000 1551893993068.000    134.000
194   621711.000 1551893993202.000  50544.000
540   621711.000 1551894043746.000    853.000
541   621711.000 1551894044599.000    262.000
542   621711.000 1551894044861.000    139.000
543   621711.000 1551894045000.000    123.000
544   621711.000 1551894045123.000    118.000
545   621711.000 1551894045241.000    145.000
546   621711.000 1551894045386.000    158.000
547   621711.000 1551894045544.000  50471.000
889   621711.000 1551894096015.000    735.000
890   621711.000 1551894096750.000    146.000
891   621711.000 1551894096896.000    138.000
892   621711.000 1551894097034.000    144.000
893   621711.000 1551894097178.000    138.000
894   621711.000 1551894097316.000    139.000
895   621711.000 1551894097455.000    310.000
896   621711.000 1551894097765.000  88898.000
1329  621711.000 1551894186663.000    698.000
1330  621711.000 1551894187361.000    154.000
1331  621711.000 1551894187515.000    144.000
1332  621711.000 1551894187659.000    139.000
1333  621711.000 1551894187798.000    123.000
1334  621711.000 1551894187921.000    127.000
1335  621711.000 1551894188048.000    142.000
1336  621711.000 1551894188190.000  50708.000
1687  621711.000 1551894238898.000   1130.000
1688  621711.000 1551894240028.000    131.000
1689  621711.000 1551894240159.000    120.000
1690  621711.000 1551894240279.000    125.000
1691  621711.000 1551894240404.000    141.000
1692  621711.000 1551894240545.000    129.000
1693  621711.000 1551894240674.000    136.000
1694  621711.000 1551894240810.000  37242.000
1916  621711.000 1551894278052.000    693.000
1917  621711.000 1551894278745.000    132.000
1918  621711.000 1551894278877.000    122.000
1919  621711.000 1551894278999.000    142.000
1920  621711.000 1551894279141.000    123.000
1921  621711.000 1551894279264.000    130.000
1922  621711.000 1551894279394.000    151.000
1923  621711.000 1551894279545.000 125163.000
2250  621711.000 1551894404708.000    749.000
2251  621711.000 1551894405457.000    169.000
2252  621711.000 1551894405626.000    151.000
2253  621711.000 1551894405777.000    131.000
2254  621711.000 1551894405908.000    129.000
2255  621711.000 1551894406037.000    148.000
2256  621711.000 1551894406185.000    143.000
2257  621711.000 1551894406328.000  50753.000
2570  621711.000 1551894457081.000    965.000
2571  621711.000 1551894458046.000    109.000
2572  621711.000 1551894458155.000    126.000
2573  621711.000 1551894458281.000    129.000
2574  621711.000 1551894458410.000  50992.000
2842  621711.000 1551894509402.000    882.000
2843  621711.000 1551894510284.000    150.000
2844  621711.000 1551894510434.000    121.000
2845  621711.000 1551894510555.000    135.000
2846  621711.000 1551894510690.000    112.000
2847  621711.000 1551894510802.000    118.000
2848  621711.000 1551894510920.000    113.000
2849  621711.000 1551894511033.000  66962.000
3216  621711.000 1551894577995.000    711.000
3217  621711.000 1551894578706.000    110.000
3218  621711.000 1551894578816.000    145.000
3219  621711.000 1551894578961.000    118.000
3220  621711.000 1551894579079.000    115.000
3221  621711.000 1551894579194.000    118.000
3222  621711.000 1551894579312.000  50915.000
3546  621711.000 1551894630227.000    579.000
3547  621711.000 1551894630806.000    124.000
3548  621711.000 1551894630930.000    125.000
3549  621711.000 1551894631055.000    125.000
3550  621711.000 1551894631180.000    144.000
3551  621711.000 1551894631324.000    143.000
3552  621711.000 1551894631467.000    150.000
3553  621711.000 1551894631617.000  37800.000
3770  621711.000 1551894669417.000    810.000
3771  621711.000 1551894670227.000    107.000
3772  621711

In [36]:
#merged = rod_group.merge(a, left_index=True, right_index=True)
#merged = merged.set_index('index')[['latency']]
#merged.head(10000)
1551894297375.000 - 1551894297225.000

150.0

In [41]:
#data_rod = data_rod.sort_index().sort_values(['id', 'start_time'])
data_rod['latency'] = rod_group['latency'] 
data_rod.head(10000)

id  price_displayed  key pressed environment     order  \
187   621711.000              nan       39.000        high  high-low   
188   621711.000              nan       39.000        high  high-low   
189   621711.000              nan       39.000        high  high-low   
190   621711.000              nan       39.000        high  high-low   
191   621711.000              nan       39.000        high  high-low   
192   621711.000              nan       39.000        high  high-low   
193   621711.000              nan       39.000        high  high-low   
194   621711.000              nan       39.000        high  high-low   
540   621711.000              nan       39.000        high  high-low   
541   621711.000              nan       39.000        high  high-low   
542   621711.000              nan       39.000        high  high-low   
543   621711.000              nan       39.000        high  high-low   
544   621711.000              nan       39.000        high  high-low   
545   621711.000              nan       39.000        high  high-low   
546   621711.000              nan       39.000        high  high-low   
547   621711.000              nan       39.000        high  high-low   
889   621711.000              nan       39.000        high  high-low   
890   621711.000              nan       39.000        high  high-low   
891   621711.000              nan       39.000        high  high-low   
892   621711.000              nan       39.000        high  high-low   
893   621711.000              nan       39.000        high  high-low   
894   621711.000              nan       39.000        high  high-low   
895   621711.000              nan       39.000        high  high-low   
896   621711.000              nan       39.000        high  high-low   
1329  621711.000              nan       39.000        high  high-low   
1330  621711.000              nan       39.000        high  high-low   
1331  621711.000              nan       39.000        high  high-low   
1332  621711.000              nan       39.000        high  high-low   
1333  621711.000              nan       39.000        high  high-low   
1334  621711.000              nan       39.000        high  high-low   
1335  621711.000              nan       39.000        high  high-low   
1336  621711.000              nan       39.000        high  high-low   
1687  621711.000              nan       39.000        high  high-low   
1688  621711.000              nan       39.000        high  high-low   
1689  621711.000              nan       39.000        high  high-low   
1690  621711.000              nan       39.000        high  high-low   
1691  621711.000              nan       39.000        high  high-low   
1692  621711.000              nan       39.000        high  high-low   
1693  621711.000              nan       39.000        high  high-low   
1694  621711.000              nan       39.000        high  high-low   
1916  621711.000              nan       39.000        high  high-low   
1917  621711.000              nan       39.000        high  high-low   
1918  621711.000              nan       39.000        high  high-low   
1919  621711.000              nan       39.000        high  high-low   
1920  621711.000              nan       39.000        high  high-low   
1921  621711.000              nan       39.000        high  high-low   
1922  621711.000              nan       39.000        high  high-low   
1923  621711.000              nan       39.000        high  high-low   
2250  621711.000              nan       39.000         low  high-low   
2251  621711.000              nan       39.000         low  high-low   
2252  621711.000              nan       39.000         low  high-low   
2253  621711.000              nan       39.000         low  high-low   
2254  621711.000              nan       39.000         low  high-low   
2255  621711.000              nan       39.000         low  high-low   
2256  621711.000              nan       39.000        

In [37]:
data_rod.to_csv("rod_no_drop.csv", sep=',', encoding='utf-8')

In [49]:
data_rod.groupby('id')['start_time'].size()

id
621711.000     91
621725.000     84
621729.000     83
621733.000     94
621734.000     92
621735.000     79
621738.000     88
621749.000     92
621753.000     94
621759.000     95
621761.000     92
621762.000     87
621770.000     90
621772.000     97
621774.000    101
621775.000     94
621785.000     89
621789.000     85
625385.000     86
625386.000     96
625389.000     90
625392.000     86
625394.000     92
625395.000    110
625403.000     75
625404.000     85
625406.000     83
625408.000     84
625410.000    113
625411.000     84
625416.000     79
625431.000     94
Name: start_time, dtype: int64

In [48]:
8 * 6 * 32

1536

In [ ]:
ser = data_rod['latency']
k = 8
to_ret = []
lst = ser.tolist()
chunks = [lst[x:x+k] for x in range(0, len(lst), k)]
for c in chunks:
    to_ret = to_ret + c[1:-1]
len(to_ret)

In [38]:
def drop_first_last (ser, k):
    """
    ser is a series from your data frame
    k - how many taps to fix the rod
    return a list of lists without the first and last tap
    """
    to_ret = []
    lst = ser.tolist()
    chunks = [lst[x:x+k] for x in range(0, len(lst), k)]
    for c in chunks:
        to_ret = to_ret + c[1:-1]
    
    return to_ret


In [ ]:
# dont know why it doesnt work
#for column in data_rod:
#    column = drop_first_last(column, 8)

In [40]:
data_rod.iloc[::8, :]

id  price_displayed  key pressed environment     order  \
187   621711.000              nan       39.000        high  high-low   
540   621711.000              nan       39.000        high  high-low   
889   621711.000              nan       39.000        high  high-low   
1329  621711.000              nan       39.000        high  high-low   
1687  621711.000              nan       39.000        high  high-low   
1916  621711.000              nan       39.000        high  high-low   
2250  621711.000              nan       39.000         low  high-low   
2570  621711.000              nan       39.000         low  high-low   
2845  621711.000              nan       39.000         low  high-low   
3219  621711.000              nan       39.000         low  high-low   
3550  621711.000              nan       39.000         low  high-low   
3774  621711.000              nan       39.000         low  high-low   
184   621725.000              nan       39.000         low  low-high   
548   621725.000              nan       39.000         low  low-high   
901   621725.000              nan       39.000         low  low-high   
1369  621725.000              nan       39.000         low  low-high   
1723  621725.000              nan       39.000         low  low-high   
1983  621725.000              nan       39.000         low  low-high   
2339  621725.000              nan       39.000        high  high-low   
2719  621725.000              nan       39.000        high  high-low   
3062  621725.000              nan       39.000        high  high-low   
4126  621725.000              nan       39.000        high  high-low   
4073  621729.000              nan       39.000        high  high-low   
4700  621729.000              nan       39.000        high  high-low   
5066  621729.000              nan       39.000        high  high-low   
5374  621729.000              nan       39.000        high  high-low   
5922  621729.000              nan       39.000         low  high-low   
6236  621729.000              nan       40.000         low  high-low   
6247  621729.000              nan       39.000         low  high-low   
6574  621729.000              nan       39.000         low  high-low   
7266  621729.000              nan       39.000         low  high-low   
7511  621729.000              nan       39.000         low  high-low   
6241  621729.000              nan          nan         low  high-low   
8579  621733.000              nan       39.000         low  low-high   
8861  621733.000              nan       39.000         low  low-high   
9117  621733.000              nan       39.000         low  low-high   
9403  621733.000              nan       39.000         low  low-high   
9571  621733.000              nan       39.000         low  low-high   
9767  621733.000              nan       39.000         low  low-high   
10196 621733.000              nan       39.000        high  high-low   
10387 621733.000              nan       39.000        high  high-low   
10711 621733.000              nan       39.000        high  high-low   
10971 621733.000              nan       39.000        high  high-low   
11118 621733.000              nan       39.000        high  high-low   
7841  621734.000              nan       39.000        high  high-low   
8174  621734.000              nan       39.000        high  high-low   
8504  621734.000              nan       39.000        high  high-low   
8916  621734.000              nan       39.000        high  high-low   
9230  621734.000              nan       39.000        high  high-low   
9466  621734.000              nan       39.000        high  high-low   
9778  621734.000              nan       39.000         low  high-low   
10076 621734.000              nan       39.000         low  high-low   
10357 621734.000              nan       39.000         low  high-low   
10737 621734.000              nan       39.000         low  high-low   
11058 621734.000              nan       39.000        

In [39]:
latency = drop_first_last(data_rod['latency'], 8)
id_e = drop_first_last(data_rod['id'], 8)
environment = drop_first_last(data_rod['environment'], 8)
round_instance = drop_first_last(data_rod['round_instance'], 8)
quality_check = drop_first_last(data_rod['quality_check'], 8)
start_time = drop_first_last(data_rod['start_time'], 8)
end_time = drop_first_last(data_rod['end_time'], 8)
d = {'id': id_e, 'environment': environment, 'round_instance': round_instance, 'quality_check': quality_check,
    'start_time': start_time, 'end_time':end_time, 'latency': latency}
data_rod_final = pd.DataFrame(data=d)
data_rod_final.head(1000)
#data_rod.head(1000)

id environment  round_instance  quality_check        start_time  \
0   621711.000        high          11.000          1.000 1551893992389.000   
1   621711.000        high          11.000          1.000 1551893992527.000   
2   621711.000        high          11.000          1.000 1551893992669.000   
3   621711.000        high          11.000          1.000 1551893992792.000   
4   621711.000        high          11.000          1.000 1551893992933.000   
5   621711.000        high          11.000          1.000 1551893993068.000   
6   621711.000        high          11.000          1.000 1551894044599.000   
7   621711.000        high          11.000          1.000 1551894044861.000   
8   621711.000        high          11.000          1.000 1551894045000.000   
9   621711.000        high          11.000          1.000 1551894045123.000   
10  621711.000        high          11.000          1.000 1551894045241.000   
11  621711.000        high          11.000          1.000 1551894045386.000   
12  621711.000        high          11.000          1.000 1551894096750.000   
13  621711.000        high          11.000          1.000 1551894096896.000   
14  621711.000        high          11.000          1.000 1551894097034.000   
15  621711.000        high          11.000          1.000 1551894097178.000   
16  621711.000        high          11.000          1.000 1551894097316.000   
17  621711.000        high          11.000          1.000 1551894097455.000   
18  621711.000        high          21.000          1.000 1551894187361.000   
19  621711.000        high          21.000          1.000 1551894187515.000   
20  621711.000        high          21.000          1.000 1551894187659.000   
21  621711.000        high          21.000          1.000 1551894187798.000   
22  621711.000        high          21.000          1.000 1551894187921.000   
23  621711.000        high          21.000          1.000 1551894188048.000   
24  621711.000        high          21.000          1.000 1551894240028.000   
25  621711.000        high          21.000          1.000 1551894240159.000   
26  621711.000        high          21.000          1.000 1551894240279.000   
27  621711.000        high          21.000          1.000 1551894240404.000   
28  621711.000        high          21.000          1.000 1551894240545.000   
29  621711.000        high          21.000          1.000 1551894240674.000   
30  621711.000        high          21.000          1.000 1551894278745.000   
31  621711.000        high          21.000          1.000 1551894278877.000   
32  621711.000        high          21.000          1.000 1551894278999.000   
33  621711.000        high          21.000          1.000 1551894279141.000   
34  621711.000        high          21.000          1.000 1551894279264.000   
35  621711.000        high          21.000          1.000 1551894279394.000   
36  621711.000         low          12.000          1.000 1551894405457.000   
37  621711.000         low          12.000          1.000 1551894405626.000   
38  621711.000         low          12.000          1.000 1551894405777.000   
39  621711.000         low          12.000          1.000 1551894405908.000   
40  621711.000         low          12.000          1.000 1551894406037.000   
41  621711.000         low          12.000          1.000 1551894406185.000   
42  621711.000         low          12.000          1.000 1551894458046.000   
43  621711.000         low          12.000          1.000 1551894458155.000   
44  621711.000         low          12.000          1.000 1551894458281.000   
45  621711.000         low          12.000          1.000 1551894458410.000   
46  621711.000         low          12.000          1.000 1551894509402.000   
47  621711.000         low          12.000          1.000 1551894510284.000   
48  621711.000         low          12.000          1.000 1551894510690.000   
49  621711.000         low          12.000          1.000 1551

In [ ]:
data_rod_final.to_csv('data_rod_pilot35.csv', sep=',', encoding='utf-8')

In [ ]:
#data_fish_l_12['start_time'].diff().describe()

In [ ]:
#data_fish_l_12['latency'].describe()

In [ ]:
#just to look at fishing data
data_fish = data[(data.function_id == 'fishing_h')|(data.function_id == 'fishing_l')]

In [ ]:
#take a look at low environment
data_fish_l = data_fish[data_fish.function_id == "fishing_l"]
#data_fish_l.head(500)

In [ ]:
#take a look at 11 and 21 seperately (11, 21 are both instances of low environment)
data_fish_l_11 = data_fish_l[data_fish_l.round_instance == 11]
data_fish_l_21 = data_fish_l[data_fish_l.round_instance == 21]
data_fish_l_12 = data_fish_l[data_fish_l.round_instance == 12]
data_fish_l_22 = data_fish_l[data_fish_l.round_instance == 22]

In [ ]:
# compute latency for each environment - round pair
data_fish_l_12['latency'] = latency(data_fish_l_12["start_time"])
data_fish_l_11['latency'] = latency(data_fish_l_11["start_time"])
data_fish_l_22['latency'] = latency(data_fish_l_22["start_time"])
data_fish_l_21['latency'] = latency(data_fish_l_21["start_time"])

In [ ]:
# put all instances of low environment into one data frame
data_fish_l = data_fish_l_11.append([data_fish_l_12, data_fish_l_22, data_fish_l_21])
data_fish_l['latency'].describe()


In [ ]:
#take a look at high environment
data_fish_h = data_fish[data_fish.function_id == "fishing_h"]
data_fish_h_12 = data_fish_h[data_fish_h.round_instance == 12]
data_fish_h_22 = data_fish_h[data_fish_h.round_instance == 22]
data_fish_h_21 = data_fish_h[data_fish_h.round_instance == 21]
data_fish_h_11 = data_fish_h[data_fish_h.round_instance == 11]

In [ ]:
# compute latency for each environment - round pair
data_fish_h_12['latency'] = latency(data_fish_h_12["start_time"])
data_fish_h_11['latency'] = latency(data_fish_h_11["start_time"])
data_fish_h_22['latency'] = latency(data_fish_h_22["start_time"])
data_fish_h_21['latency'] = latency(data_fish_h_21["start_time"])

In [ ]:
# put all instances of high environment into one data frame
data_fish_h = data_fish_h_11.append([data_fish_h_12, data_fish_h_22, data_fish_h_21])

In [ ]:
pd.set_option('display.max_columns', 300)
pd.set_option('display.max_rows', None)
#data_fish_h

In [ ]:
nan_rows = data_fish_h[data_fish_h['latency'].isnull()]
nan_rows

In [ ]:
data_raw = data_fish_l.append(data_fish_h)


In [ ]:
#low environment
low_price = data_fish_l['price_displayed']
low_tap = np.arange(1, len(data_fish_l['price_displayed'])+1)
low_latency = data_fish_l['latency']


In [ ]:
fig, ax1 = plt.subplots()

color = 'tab:blue'
ax1.set_xlabel('tap (n)')
ax1.set_ylabel('latency (ms)')
ax1.plot(low_tap, low_latency, color=color)
ax1.set_ylim([0,3000])
ax1.tick_params(axis='y', labelcolor=color)

ax2 = ax1.twinx()  # instantiate a second axes that shares the same x-axis

color = 'tab:red'
ax2.set_ylabel('price')  # we already handled the x-label with ax1
ax2.scatter(low_tap, low_price, color=color, s = 1)
ax2.tick_params(axis='y', labelcolor=color)

fig.tight_layout()  # otherwise the right y-label is slightly clipped
plt.show()

In [ ]:
#high environment
high_price = data_fish_h['price_displayed']
high_tap = np.arange(1, len(data_fish_h['price_displayed'])+1)
high_latency = data_fish_h['latency']

In [ ]:
fig, ax1 = plt.subplots()

color = 'tab:blue'
ax1.set_xlabel('tap (n)')
ax1.set_ylabel('latency (ms)')
ax1.plot(high_tap, high_latency, color=color)
ax1.set_ylim([300,3000])
ax1.tick_params(axis='y', labelcolor=color)

ax2 = ax1.twinx()  # instantiate a second axes that shares the same x-axis

color = 'tab:red'
ax2.set_ylabel('price')  # we already handled the x-label with ax1
ax2.scatter(high_tap, high_price, color=color, s = 1)
ax2.tick_params(axis='y', labelcolor=color)

fig.tight_layout()  # otherwise the right y-label is slightly clipped
plt.show()

In [ ]:
data = data_raw[(data_row['latency'] > 0)&(data_row['latency']<3000)]  
#data_row['latency'].describe()


In [ ]:
#104305-104122

In [ ]:
#data['latency'].describe() # dropped 183 data points

In [ ]:
bonus = data.groupby(["Participant Public ID","price_displayed", "function_id"]).size()
bonus = bonus.reset_index()
bonus.columns = ['Participant Public ID', 'price_displayed', 'factor', 'tap']
bonus = bonus.replace('fishing_h', 4/3000)
bonus = bonus.replace('fishing_l', 0.5/3000)
bonus = bonus.round(20)
bonus['earning'] = bonus['price_displayed']*bonus['factor']*bonus['tap']
pay = bonus.groupby(['Participant Public ID'])['earning'].sum().reset_index()
pay['earning'] = np.ceil(pay['earning'])
pay['prolific'] = [','.join(i) for i in zip(pay["Participant Public ID"].map(str),pay["earning"].astype(str))]
pay
pay.to_csv('prolific_bonus.csv', sep = ',', encoding='utf-8')



In [ ]:
graph = data.groupby(["price_displayed", "function_id"])['latency'].mean().reset_index()
graph.columns = ['price_displayed', 'function_id', 'average_latency']
graph

In [ ]:
price = [0.1, 0.3, 0.7, 1.2, 1.8, 2.5]
latency_l = [214.188, 201.843, 195.058, 189.166, 185.015, 179.721]
latency_h = [199.484, 190.566, 188.765, 180.929, 178.948, 174.016]

In [ ]:
plt.plot( price, latency_l, marker='', color='purple', linewidth=2, label = "low")
plt.plot( price, latency_h, marker='', color='black', linewidth=2, linestyle='dashed', label="high")
plt.legend()
#look at low-high and high-low for transition period
#understand the variance within the data and think about if the variables in the model can explain them

In [ ]:
# do a quick check for sound
sound = pd.read_csv('data_exp_6138-v31_task-jgum.csv', sep = ",")
sound = sound.replace('null', np.nan)
sound = sound.replace('nan', np.nan)
#sound.head(40)

In [ ]:
sound['button pressed'].dropna()
correct = [1, 0, 0]* 32

In [ ]:
sound['button pressed'].dropna() == correct

In [ ]:
data.to_csv("pilot35.csv", sep=',', encoding='utf-8')

In [ ]:
# import AMI
AMI = pd.read_csv('data_exp_6138-v31_task-lgcm.csv', sep = ",")
AMI

In [ ]:
#get rid of the last line - does not contain any infomraiton
#AMI = AMI[:-1]
#AMI.head(100)

In [ ]:
#AMI["choice made"]

In [ ]:
AMI_group = AMI.groupby(["Participant Private ID"])['choice made'].apply(list).reset_index()
response = AMI_group['choice made'][0]
AMI_group.head(10)

In [ ]:
#response = AMI_group['choice made'][0]
#d['hi'] = d.pop('hii')
#response[0] = json.loads(response[0])
#response[0]['Q1'] = response[0]['Q0']
#del response[0]['Q0']
#print (response)

In [ ]:
def extract_choice(ser):
    choice = []
    for s in ser:
        c = 0
        while c < len(s):
            r = json.loads(s[c])
            for key in r.keys():
                choice.append(r[key])
            c = c + 1
    return choice

In [ ]:
#len(extract_choice(AMI_group['choice made']))

In [ ]:
choice = extract_choice(AMI_group['choice made'])
# comment the next line off so you dont repeat the command multiple times
#AMI_group = AMI_group.loc[AMI_group.index.repeat(18)]
len(AMI_group)

In [ ]:
AMI_group['choice'] = choice

In [ ]:
AMI_group['question_number'] = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18]*32

In [ ]:
AMI_group.head(10)

In [ ]:
AMI_group.choice[AMI_group.choice == "Completely UNTRUE"] = 4
AMI_group.choice[AMI_group.choice == "Mostly untrue"] = 3
AMI_group.choice[AMI_group.choice == "Neither true nor untrue"] = 2
AMI_group.choice[AMI_group.choice == "Quite true"] = 1
AMI_group.choice[AMI_group.choice == "Completely TRUE"] = 0

In [ ]:
# bAMI = questions [5 9 10 11 12 15]
# sAMI = questions [2 3 4  8  14 17]
# eAMI = questions [1 6 7  13 16 18]
# tAMI = sum
bAMI = AMI_group[(AMI_group.question_number == 5)|(AMI_group.question_number == 9)|(AMI_group.question_number == 10)|(AMI_group.question_number == 11)|(AMI_group.question_number == 12)|(AMI_group.question_number == 15)]
sAMI = AMI_group[(AMI_group.question_number == 2)|(AMI_group.question_number == 3)|(AMI_group.question_number == 4)|(AMI_group.question_number == 8)|(AMI_group.question_number == 14)|(AMI_group.question_number == 17)]
eAMI = AMI_group[(AMI_group.question_number == 1)|(AMI_group.question_number == 6)|(AMI_group.question_number == 7)|(AMI_group.question_number == 13)|(AMI_group.question_number == 16)|(AMI_group.question_number == 18)]
bAMI = bAMI.groupby(['Participant Private ID'])['choice'].sum().reset_index()
bAMI.columns = ['id', 'bAMI']
sAMI = sAMI.groupby(['Participant Private ID'])['choice'].sum().reset_index()
sAMI.columns = ['id', 'sAMI']
eAMI = eAMI.groupby(['Participant Private ID'])['choice'].sum().reset_index()
eAMI.columns = ['id', 'eAMI']
AMI_final = {'id': bAMI['id'], 'bAMI': bAMI['bAMI'], 'sAMI': sAMI['sAMI'], 'eAMI': eAMI['eAMI']}
AMI_final = pd.DataFrame(data=AMI_final)
AMI_final['tAMI'] = bAMI['bAMI'] + sAMI['sAMI'] + eAMI['eAMI']
AMI_final

In [ ]:
AMI_final.to_csv('AMI35.csv', sep=',', encoding='utf-8')

In [ ]:
plt.scatter(AMI_final.index.tolist(), AMI_final['tAMI'], color='purple')
plt.legend()
#look at and interpret each data point
#find examplar subjects and understand their behavior

In [ ]:
# import HAD
HAD = pd.read_csv('data_exp_6138-v31_task-w8es.csv', sep = ",")
HAD.head(5)

In [ ]:
HAD_group = HAD.groupby(["Participant Private ID"])['choice made'].apply(list).reset_index()
HAD_group.head(10)

In [ ]:
choice = extract_choice(HAD_group['choice made'])
# comment the next line off so you dont repeat the command multiple times
#HAD_group = HAD_group.loc[HAD_group.index.repeat(14)]



In [ ]:
HAD_group['choice'] = choice
HAD_group['question_number'] = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14]*32

In [ ]:
HAD_group['scale'] = [{"Most of the time" : 3, "A lot of the time": 2, "From time to time, occasionally" : 1, "Not at all":0},
                      {"Nearly all the time": 3, "Very often": 2, "Sometimes": 1, "Not at all":0},
                      {"Definitely as much":0, "Not quite so much":1, "Only a little":2, "Hardly at all":3},
                      {"Not at all":0, "Occasionally":1, "Quite Often":2, "Very Often":3},
                      {"Very definitely and quite badly":3, "Yes, but not too badly":2, "A little, but it doesn't worry me":1, "Not at all":0},
                      {"Definitely":3, "I don't take as much care as I should":2,"I may not take quite as much care":1, "I take just as much care as ever":0},
                      {"As much as I always could":0, "Not quite so much now":1, "Definitely not so much now":2, "Not at all":3},
                      {"Very much indeed":3, "Quite a lot":2,"Not very much":1, "Not at all":0},
                      {"A great deal of the time":3, "A lot of the time":2, "From time to time, but not too often":1,"Only occasionally":0},
                      {"As much as I ever did":0, "Rather less than I used to":1, "Definitely less than I used to":2, "Hardly at all":3},
                      {"Not at all":3, "Not often":2,"Sometimes":1, "Most of the time":0},
                      {"Very often indeed":3, "Quite often":2,"Not very often":1, "Not at all":0},
                      {"Definitely":0, "Usually":1, "Not Often":2,"Not at all":3},
                      {"Often":0, "Sometimes":1,"Not often":2, "Very seldom":3}]*32

In [ ]:
# 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14
# A, D, D, A, A, D, D, A, A, D,   D,  A,  A, D

# anxiety =  [1, 4, 5, 8, 9, 12, 13]
# depression = [2, 3, 6, 7, 10, 11, 14]
depression = HAD_group[(HAD_group.question_number == 2)|(HAD_group.question_number == 3)|(HAD_group.question_number == 6)|(HAD_group.question_number == 7)|(HAD_group.question_number == 10)|(HAD_group.question_number == 11)|(HAD_group.question_number == 14)]
anxiety = HAD_group[(HAD_group.question_number == 1)|(HAD_group.question_number == 4)|(HAD_group.question_number == 5)|(HAD_group.question_number == 8)|(HAD_group.question_number == 9)|(HAD_group.question_number == 12)|(HAD_group.question_number == 13)]

value = []
for index, row in HAD_group.iterrows():
    d = row["scale"]
    k = row['choice']
    value.append(d[k])
HAD_group['value'] = value



In [ ]:
depression = depression.groupby(['Participant Private ID'])['value'].sum().reset_index()
depression.columns = ['id', 'depression']
anxiety = anxiety.groupby(['Participant Private ID'])['value'].sum().reset_index()
anxiety.columns = ['id', 'anxiety']
HAD_group.head(5)

In [ ]:
HAD_final = {'id': anxiety['id'], 'anxiety': anxiety['anxiety'], 'depression': depression['depression']}
HAD_final = pd.DataFrame(data=HAD_final)
HAD_final['tHAD'] = anxiety['anxiety'] + depression['depression']

HAD_final.to_csv('HAD_pilot35.csv', sep = ',', encoding='utf-8')
HAD_final.head(10)

In [ ]:

AMI_group.choice[AMI_group.choice == "Completely UNTRUE"] = 4
AMI_group.choice[AMI_group.choice == "Mostly untrue"] = 3
AMI_group.choice[AMI_group.choice == "Neither true nor untrue"] = 2
AMI_group.choice[AMI_group.choice == "Quite true"] = 1
AMI_group.choice[AMI_group.choice == "Completely TRUE"] = 0

In [ ]:
demographics = pd.read_csv('data_exp_6138-v31_questionnaire-zk38.csv', sep = ",")
demographics.head(15)
# we asked them 7 questions in total




In [ ]:
demographics = demographics[demographics['Question Key'] != 'BEGIN QUESTIONNAIRE']
demographics = demographics[demographics['Question Key'] != 'END QUESTIONNAIRE']
demographics['id'] = demographics['Participant Private ID']
demographics['question'] = demographics['Question Key']
demographics['response'] = demographics['Response']
demographics = demographics[['id', 'question', 'response']]
demographics.head(33)



In [ ]:
demographics.to_csv('demographics.csv', sep = ',', encoding='utf-8')

In [ ]:
#artifact in second tap of rod fixing & NaNs - send Akshay Pesudo code
#age limit: 25 - 65
#the payment strucutre - decrease hourly rate and keep the bonus the same